In [1]:
import os
import numpy as np
import matplotlib.pyplot as plt
import tqdm
import torch
import json
import requests
import networkx as nx
import matplotlib.pyplot as plt
import plotly.graph_objects as go
from collections import defaultdict, Counter
from itertools import combinations
import datetime
import matplotlib.pyplot as plt



import sys


ProjectPath = "/home/liranc6/con_graph"
sys.path.append(ProjectPath)  # Add the parent directory to the sys.path

In [2]:
os.environ['CUDA_DEVICE_ORDER'] = 'PCI_BUS_ID'
os.environ['CUDA_VISIBLE_DEVICES'] = '5'

! gpustat

rambo6                      Tue Apr 23 08:44:35 2024  525.147.05
[0] NVIDIA GeForce RTX 3090 | 25°C,   0 % |     1 / 24576 MB |
[1] NVIDIA GeForce RTX 3090 | 25°C,   0 % |     1 / 24576 MB |
[2] NVIDIA GeForce RTX 3090 | 25°C,   0 % |     1 / 24576 MB |
[3] NVIDIA GeForce RTX 3090 | 23°C,   0 % |     1 / 24576 MB |
[4] NVIDIA GeForce RTX 3090 | 24°C,   0 % |     1 / 24576 MB |
[5] NVIDIA GeForce RTX 3090 | 25°C,   0 % |     1 / 24576 MB |
[6] NVIDIA GeForce RTX 3090 | 25°C,   0 % |     1 / 24576 MB |
[7] NVIDIA GeForce RTX 3090 | 24°C,   0 % |     1 / 24576 MB |


In [3]:
def get_metadata(data_path):
    with open(data_path, 'r') as f:
        for line in f:
            metadata = json.loads(line)
            yield metadata

In [4]:
# Sample raw data
dataset = "/mnt/qnap/liranc6/data/con_graph/dataset/subset_metadata_with_concepts.json"
for i, line in enumerate(get_metadata(dataset)):
    print(line)
    break

{'id': '0906.4492', 'title': 'Efficient Generation of Craig Interpolants in Satisfiability Modulo\n  Theories', 'abstract': '  The problem of computing Craig Interpolants has recently received a lot of\ninterest. In this paper, we address the problem of efficient generation of\ninterpolants for some important fragments of first order logic, which are\namenable for effective decision procedures, called Satisfiability Modulo Theory\nsolvers.\n  We make the following contributions.\n  First, we provide interpolation procedures for several basic theories of\ninterest: the theories of linear arithmetic over the rationals, difference\nlogic over rationals and integers, and UTVPI over rationals and integers.\n  Second, we define a novel approach to interpolate combinations of theories,\nthat applies to the Delayed Theory Combination approach.\n  Efficiency is ensured by the fact that the proposed interpolation algorithms\nextend state of the art algorithms for Satisfiability Modulo Theories. 

In [96]:
def build_graph2(dataset):
    # Create an empty graph
    G = nx.MultiGraph()
    
    # papers_published = defaultdict(lambda: defaultdict(int))

    # Add nodes
    for idx, paper in enumerate(get_metadata(dataset)):
        keywords = paper['concepts']
        paper_submit_date = (paper['submit_date'][1], paper['submit_date'][0])

        # Add a node for each keyword if it doesn't already exist
        for word in keywords:
            if word not in G.nodes:
                G.add_node(word, num_papers=1, min_publish_date=paper_submit_date)
            else:
                G.nodes[word]['num_papers'] += 1
                if G.nodes[word]['min_publish_date'] > paper_submit_date:
                    G.nodes[word]['min_publish_date'] = paper_submit_date
        
        # Add edges between each pair of nodes in the current sublist
        for i in range(len(keywords)):
            #chack if edge already exists with this date
            for j in range(i+1, len(keywords)):
                if G.has_edge(keywords[i], keywords[j]) and paper_submit_date in G[keywords[i]][keywords[j]]:
                    G[keywords[i]][keywords[j]][paper_submit_date]['num_papers'] += 1
                else:
                    G.add_edge(keywords[i], keywords[j], date=paper_submit_date, num_papers=1)            
            
        # if idx > 3500:
            # break
    
    #set attributes to nodes
    for node in G.nodes:
        #for edge connected to node
        min_publish_date = G.nodes[node]['min_publish_date']
        now_year, now_month = datetime.datetime.now().year, datetime.datetime.now().month
        age_in_months = (now_year - min_publish_date[0])*12 + (now_month - min_publish_date[1])
        if now_month < min_publish_date[0]:
            age_in_months += 12
        G.nodes[node]['age_in_months'] = age_in_months

        num_connected_nodes = len(list(G.neighbors(node)))

        alpha = 0.3
        betha = 0.4
        assert alpha + betha <= 1
        G.nodes[node]['num_connected_nodes'] = num_connected_nodes
        G.nodes[node]['hierarchy_score'] = alpha * G.nodes[node]['num_papers'] +  betha * G.nodes[node]['num_connected_nodes'] + (1-alpha-betha) * G.nodes[node]['age_in_months']
    return G
G = build_graph2(dataset)

In [150]:
def get_nodes_and_scores(G):
    lst = []
    for node in G.nodes:
        lst.append((G.nodes[node]['hierarchy_score'], node))
    lst.sort(reverse=True)
    return lst

nodes = get_nodes_and_scores(G)
nodes[:20]

[(3121.6000000000004, 'machine learning'),
 (2876.8, 'graph theory'),
 (2149.2, 'artificial intelligence'),
 (1901.0, 'distributed systems'),
 (1859.8, 'computer science'),
 (1815.0, 'computational complexity'),
 (1631.2000000000003, 'information theory'),
 (1573.6, 'algorithm design'),
 (1348.6, 'wireless communication'),
 (1253.8000000000002, 'computer vision'),
 (1249.8, 'computer networks'),
 (1236.4, 'wireless networks'),
 (1100.6000000000001, 'signal processing'),
 (1075.0, 'natural language processing'),
 (989.2, 'game theory'),
 (938.8000000000001, 'image processing'),
 (817.2, 'network analysis'),
 (801.4000000000001, 'cryptography'),
 (776.0, 'optimization techniques'),
 (768.8, 'computational geometry')]

In [58]:
def build_graph(dataset):
    papers_published = defaultdict(lambda: defaultdict(int))
    G = {"nodes": [], "edges": []}

    for idx, paper in enumerate(get_metadata(dataset)):
        keywords = paper['concepts']
        paper_submit_date = paper['submit_date']

        for word in keywords:
            if word not in G["nodes"]:
                G["nodes"].append(word)

        for i in range(len(keywords)):
            for j in range(i + 1, len(keywords)):
                papers_published[(keywords[i], keywords[j])][tuple(paper_submit_date)] += 1

        for edge, dates in papers_published.items():
            for date, num_papers in dates.items():
                G["edges"].append((edge[0], edge[1], date, num_papers))

        if idx > 1000:
            break

    return G


# G = build_graph(dataset)

In [59]:
def viz_graph1(g):
    # Extract nodes and edges
    nodes = G["nodes"]
    edges = G["edges"]

    # Create edge traces
    edge_x = []
    edge_y = []
    for edge in edges:
        x0, y0 = nodes.index(edge[0]), nodes.index(edge[1])
        edge_x.extend([x0, x0, None])
        edge_y.extend([y0, y0, None])

    # Create node traces
    node_x = [nodes.index(node) for node in nodes]
    node_y = [0] * len(nodes)

    edge_trace = go.Scatter(
        x=edge_x, y=edge_y,
        line=dict(width=0.5, color='#888'),
        hoverinfo='none',
        mode='lines')

    node_trace = go.Scatter(
        x=node_x, y=node_y,
        mode='markers',
        hoverinfo='text',
        marker=dict(
            showscale=True,
            colorscale='YlGnBu',
            color=[],
            size=10,
            colorbar=dict(
                thickness=15,
                title='Node Connections',
                xanchor='left',
                titleside='right'
            ),
            line_width=2))

    # Add node info to hover text
    node_trace.text = [f"Node: {node}<br>#Papers: {len([edge for edge in edges if edge[0] == node or edge[1] == node])}" for node in nodes]

    fig = go.Figure(data=[edge_trace, node_trace],
                    layout=go.Layout(
                        title='<br>Interactive Graph Visualization',
                        titlefont_size=16,
                        showlegend=False,
                        hovermode='closest',
                        margin=dict(b=20, l=5, r=5, t=40),
                        annotations=[dict(
                            text="Python code adapted from: https://plotly.com/python/network-graphs/",
                            showarrow=False,
                            xref="paper", yref="paper",
                            x=0.005, y=-0.002)],
                        xaxis=dict(showgrid=False, zeroline=False, showticklabels=False),
                        yaxis=dict(showgrid=False, zeroline=False, showticklabels=False))
                    )

    fig.show()

In [149]:
def viz_graph(graph, score_range=None):
    # Create an empty undirected graph
    G = nx.Graph()

    # Add edges and their attributes (papers) to the graph
    for keyword1 in graph:
        for keyword2 in graph[keyword1]:
            papers = graph[keyword1][keyword2]
            G.add_edge(keyword1, keyword2, papers=papers)

    # Filter nodes based on score_range
    filtered_nodes = []
    for node in G.nodes():
        if score_range is None or (graph.nodes[node]['hierarchy_score'] >= score_range[0] and graph.nodes[node]['hierarchy_score'] <= score_range[1]):
            filtered_nodes.append(node)

    # Create a subgraph containing only the filtered nodes and their connections
    H = G.subgraph(filtered_nodes)

    # Draw the graph
    pos = nx.spring_layout(H)  # Positions of nodes using the spring layout algorithm

    # Define edges and positions
    edge_x = []
    edge_y = []
    for edge in H.edges():
        x0, y0 = pos[edge[0]]
        x1, y1 = pos[edge[1]]
        edge_x.extend([x0, x1, None])  # None is used to create gaps between edge segments
        edge_y.extend([y0, y1, None])

    # Create edges
    edge_trace = go.Scatter(
        x=edge_x, y=edge_y,
        line=dict(width=0.5, color='#888'),
        hoverinfo='none',
        mode='lines')

    # Create nodes
    node_x = []
    node_y = []
    node_text = []
    node_connections = []  # Store the number of connections for each node
    for node in H.nodes():
        x, y = pos[node]
        node_x.append(x)
        node_y.append(y)
        # Constructing the text to display when hovering over a node
        text = f"{node}<br>" \
               f"Hierarchy Score: {graph.nodes[node]['hierarchy_score']}<br>" \
               f"Number of Papers: {graph.nodes[node]['num_papers']}<br>" \
               f"Age in Months: {graph.nodes[node]['age_in_months']}<br>" \
               f"num_connected_nodes: {graph.nodes[node]['num_connected_nodes']}"
        node_text.append(text)
        # Count the number of connections for each node
        node_connections.append(len(H.edges(node)))

    node_trace = go.Scatter(
        x=node_x, y=node_y,
        mode='markers',
        hoverinfo='text',
        text=node_text,
        marker=dict(
            showscale=True,  # Show the color scale
            colorscale='YlGnBu',
            size=10,
            color=node_connections,  # Color nodes based on the number of connections
            colorbar=dict(title='Node Connections'),  # Title for the color bar
            line_width=2))

    # Create figure
    fig = go.Figure(data=[edge_trace, node_trace],
                    layout=go.Layout(
                        title='Interactive Graph',
                        titlefont_size=16,
                        showlegend=False,
                        hovermode='closest',
                        margin=dict(b=20, l=5, r=5, t=40),
                        xaxis=dict(showgrid=False, zeroline=False, showticklabels=False),
                        yaxis=dict(showgrid=False, zeroline=False, showticklabels=False)))

    # Show the interactive graph
    fig.show()

# Example usage:
# Draw the entire graph
# draw_graph(G)

# Draw the graph with nodes in a specific score range
viz_graph(G, score_range=(760, 40000))

In [153]:
import networkx as nx
import plotly.graph_objects as go

def viz_graph(graph, vertex, score_range=None):
    # Create an empty undirected graph
    G = nx.Graph()

    # Add edges and their attributes (papers) to the graph
    for keyword1 in graph:
        for keyword2 in graph[keyword1]:
            papers = graph[keyword1][keyword2]
            G.add_edge(keyword1, keyword2, papers=papers)

    # Determine the score of the given vertex
    vertex_score = graph.nodes[vertex]['hierarchy_score']

    # Filter nodes based on score_range
    filtered_nodes = []
    for node in G.nodes():
        if score_range is None or (
            graph.nodes[node]['hierarchy_score'] >= vertex_score - 200 and
            graph.nodes[node]['hierarchy_score'] <= vertex_score + 200
        ):
            filtered_nodes.append(node)

    # Create a subgraph containing only the filtered nodes and their connections
    H = G.subgraph(filtered_nodes)

    # Draw the graph
    pos = nx.spring_layout(H)  # Positions of nodes using the spring layout algorithm

    # Define edges and positions
    edge_x = []
    edge_y = []
    for edge in H.edges():
        x0, y0 = pos[edge[0]]
        x1, y1 = pos[edge[1]]
        edge_x.extend([x0, x1, None])  # None is used to create gaps between edge segments
        edge_y.extend([y0, y1, None])

    # Create edges
    edge_trace = go.Scatter(
        x=edge_x, y=edge_y,
        line=dict(width=0.5, color='#888'),
        hoverinfo='none',
        mode='lines')

    # Create nodes
    node_x = []
    node_y = []
    node_text = []
    node_connections = []  # Store the number of connections for each node
    for node in H.nodes():
        x, y = pos[node]
        node_x.append(x)
        node_y.append(y)
        # Constructing the text to display when hovering over a node
        text = f"{node}<br>" \
               f"Hierarchy Score: {graph.nodes[node]['hierarchy_score']}<br>" \
               f"Number of Papers: {graph.nodes[node]['num_papers']}<br>" \
               f"Age in Months: {graph.nodes[node]['age_in_months']}<br>" \
               f"num_connected_nodes: {graph.nodes[node]['num_connected_nodes']}"
        node_text.append(text)
        # Count the number of connections for each node
        node_connections.append(len(H.edges(node)))

    node_trace = go.Scatter(
        x=node_x, y=node_y,
        mode='markers',
        hoverinfo='text',
        text=node_text,
        marker=dict(
            showscale=True,  # Show the color scale
            colorscale='YlGnBu',
            size=10,
            color=node_connections,  # Color nodes based on the number of connections
            colorbar=dict(title='Node Connections'),  # Title for the color bar
            line_width=2))

    # Create figure
    fig = go.Figure(data=[edge_trace, node_trace],
                    layout=go.Layout(
                        title='Interactive Graph',
                        titlefont_size=16,
                        showlegend=False,
                        hovermode='closest',
                        margin=dict(b=20, l=5, r=5, t=40),
                        xaxis=dict(showgrid=False, zeroline=False, showticklabels=False),
                        yaxis=dict(showgrid=False, zeroline=False, showticklabels=False)))

    # Show the interactive graph
    fig.show()

# Example usage:
# Draw the graph with nodes connected to 'vertex' within a score range of ±100
viz_graph(G, 'artificial intelligence', score_range=(760, 40000))

In [159]:
import plotly.graph_objects as go
import networkx as nx

def viz_graph(graph, score_range=None):
    # Create an empty undirected graph
    G = nx.Graph()

    # Add edges and their attributes (papers) to the graph
    for keyword1 in graph:
        for keyword2 in graph[keyword1]:
            papers = graph[keyword1][keyword2]
            G.add_edge(keyword1, keyword2, papers=papers)

    # Filter nodes based on score_range
    filtered_nodes = []
    for node in G.nodes():
        if score_range is None or (graph.nodes[node]['hierarchy_score'] >= score_range[0] and graph.nodes[node]['hierarchy_score'] <= score_range[1]):
            filtered_nodes.append(node)

    # Create a subgraph containing only the filtered nodes and their connections
    H = G.subgraph(filtered_nodes)

    # Draw the graph
    pos = nx.spring_layout(H)  # Positions of nodes using the spring layout algorithm

    # Define edges and positions
    edge_x = []
    edge_y = []
    for edge in H.edges():
        x0, y0 = pos[edge[0]]
        x1, y1 = pos[edge[1]]
        edge_x.extend([x0, x1, None])  # None is used to create gaps between edge segments
        edge_y.extend([y0, y1, None])

    # Create edges
    edge_trace = go.Scatter(
        x=edge_x, y=edge_y,
        line=dict(width=0.5, color='#888'),
        hoverinfo='none',
        mode='lines')

    # Create nodes
    node_x = []
    node_y = []
    node_text = []
    node_connections = []  # Store the number of connections for each node
    for node in H.nodes():
        x, y = pos[node]
        node_x.append(x)
        node_y.append(y)
        # Constructing the text to display when hovering over a node
        text = f"{node}<br>" \
               f"Hierarchy Score: {graph.nodes[node]['hierarchy_score']}<br>" \
               f"Number of Papers: {graph.nodes[node]['num_papers']}<br>" \
               f"Age in Months: {graph.nodes[node]['age_in_months']}<br>" \
               f"num_connected_nodes: {graph.nodes[node]['num_connected_nodes']}"
        node_text.append(text)
        # Count the number of connections for each node
        node_connections.append(len(H.edges(node)))

    node_trace = go.Scatter(
        x=node_x, y=node_y,
        mode='markers',
        hoverinfo='text',
        text=node_text,
        marker=dict(
            showscale=True,  # Show the color scale
            colorscale='YlGnBu',
            size=10,
            color=node_connections,  # Color nodes based on the number of connections
            colorbar=dict(title='Score'),  # Updated title for the color bar
            line_width=2))

    # Create figure
    fig = go.Figure(data=[edge_trace, node_trace],
                    layout=go.Layout(
                        title='Interactive Graph',
                        titlefont_size=16,
                        showlegend=False,
                        hovermode='closest',
                        margin=dict(b=20, l=5, r=5, t=40),
                        xaxis=dict(showgrid=False, zeroline=False, showticklabels=False),
                        yaxis=dict(showgrid=False, zeroline=False, showticklabels=False)))

    # Show the interactive graph
    fig.show()

# Example usage:
# Draw the entire graph
# draw_graph(G)

# Draw the graph with nodes in a specific score range
viz_graph(G, score_range=(760, 40000))

In [60]:
# Plotting the graph
def viz_graph2(g):
    pos = nx.spring_layout(G)  # You can choose a different layout algorithm
    edge_trace = go.Scatter(
        x=[],
        y=[],
        line=dict(width=0.5, color='#888'),
        hoverinfo='none',
        mode='lines')

    for edge in G.edges(data=True):
        x0, y0 = pos[edge[0]]
        x1, y1 = pos[edge[1]]
        edge_trace['x'] += tuple([x0, x1, None])
        edge_trace['y'] += tuple([y0, y1, None])

    node_trace = go.Scatter(
        x=[],
        y=[],
        text=[],
        mode='markers',
        hoverinfo='text',
        marker=dict(
            showscale=True,
            colorscale='YlGnBu',
            color=[],
            size=10,
            colorbar=dict(
                thickness=15,
                title='Node Connections',
                xanchor='left',
                titleside='right'
            ),
            line_width=2))

    for node in G.nodes(data=True):
        x, y = pos[node[0]]
        node_trace['x'] += tuple([x])
        node_trace['y'] += tuple([y])
        node_info = f"Node: {node[0]}<br>#Papers: {node[1]['num_papers']}<br>Min Publish Date: {node[1]['min_publish_date']}"
        node_trace['text'] += tuple([node_info])
        node_trace['marker']['color'] += tuple([len(list(G.neighbors(node[0])))])
        
    fig = go.Figure(data=[edge_trace, node_trace],
                layout=go.Layout(
                    title='<br>Interactive Graph Visualization',
                    titlefont_size=16,
                    showlegend=False,
                    hovermode='closest',
                    margin=dict(b=20, l=5, r=5, t=40),
                    annotations=[dict(
                        text="Python code adapted from: https://plotly.com/python/network-graphs/",
                        showarrow=False,
                        xref="paper", yref="paper",
                        x=0.005, y=-0.002)],
                    xaxis=dict(showgrid=False, zeroline=False, showticklabels=False),
                    yaxis=dict(showgrid=False, zeroline=False, showticklabels=False))
                    )

    fig.show()

In [61]:
def build_graph(dataset):
    corpus = set()
    # graph = defaultdict(lambda: defaultdict(Counter))
    graph = defaultdict(lambda: defaultdict(list))
    vertex_weights = Counter()  # Counter to store weights for each vertex

    for idx, paper in enumerate(get_metadata(dataset)):
        keywords = paper['concepts']
        paper_submit_date = paper['submit_date']
        paper_id = paper['id']

        # Convert string date to datetime
        # try:
        #     paper_submit_date_str = f"{paper_submit_date[1]}-{paper_submit_date[0]:02d}"
        #     paper_submit_date = datetime.datetime.strptime(paper_submit_date_str, "%Y-%m")
        # except ValueError:
        #     print(f"Invalid date format: {paper_submit_date}")
        #     continue

        # for keyword in keywords:
        #     # Update vertex weights
        #     if vertex_weights[keyword] == 0 or paper_submit_date < vertex_weights[keyword]:
        #         vertex_weights[keyword] = paper_submit_date

        
        for keyword1, keyword2 in combinations(sorted(keywords), 2):
            # Add date to the dictionary under the respective keyword pair
            # graph[keyword1][keyword2][tuple(paper_submit_date)] += 1
            # graph[keyword2][keyword1][tuple(paper_submit_date)] += 1
            graph[keyword2][keyword1].append(paper_id)
            graph[keyword1][keyword2].append(paper_id)

        corpus.update(keywords)

        if idx > 3500:
            break

    def find_min_date(edges):
        # Extract unique tuples from the counters
        paper_submit_dates = {list(date.keys())[0] for date in edges}
        
        # Find the minimum tuple based on the second element first, then based on the first element
        min_tuple = min(paper_submit_dates, key=lambda x: (x[1], x[0]))

        print(f"{paper_submit_dates=}")
        
        return min_tuple

    def get_num_edges(edges):
        paper_submit_dates = [list(date.keys())[1] for date in edges]



    for keyword in graph:
        break
        edges = graph[keyword].values()
        graph[keyword]['earliest_date_mentioned'] = find_min_date(edges)
        print(f"{keyword}: {graph[keyword]['earliest_date_mentioned']}")
        break
        
        
    
    # Add weights to the graph for each vertex
    # for keyword in vertex_weights:
    #     graph[keyword]['weight'] = vertex_weights[keyword]

    return graph, corpus

# Build the graph
# graph, corpus = build_graph(dataset)

# len(corpus)

In [62]:
def find_min_date(edges):
        # Extract unique tuples from the counters
        paper_submit_dates = {list(date.keys())[0] for date in edges}
        
        # Find the minimum tuple based on the second element first, then based on the first element
        min_tuple = min(paper_submit_dates, key=lambda x: (x[1], x[0]))

        print(f"{paper_submit_dates=}")
        
        return min_tuple

In [63]:
# lst = graph['data analysis'].values()
# lst2 = [list(date.keys())[0] for date in graph[keyword1].values()]
# lst
# find_min_date(graph['data analysis'].values())

In [64]:
corpus_path = "/home/liranc6/con_graph/corpus.txt"
def save_corpus(corpus_path, corpus):
    with open(corpus_path, 'w') as corpus_file:
        corpus = '\n'.join(corpus)    
        corpus_file.write(corpus + '\n')

# save_corpus(corpus_path, corpus)

In [65]:
def draw_graph(graph):
    # Create an empty undirected graph
    G = nx.Graph()

    # Add edges and their attributes (papers) to the graph
    for keyword1 in graph:
        for keyword2 in graph[keyword1]:
            papers = graph[keyword1][keyword2]
            G.add_edge(keyword1, keyword2, papers=papers)

    # Draw the graph
    pos = nx.spring_layout(G)  # Positions of nodes using the spring layout algorithm

    # Define edges and positions
    edge_x = []
    edge_y = []
    for edge in G.edges():
        x0, y0 = pos[edge[0]]
        x1, y1 = pos[edge[1]]
        edge_x.extend([x0, x1, None])  # None is used to create gaps between edge segments
        edge_y.extend([y0, y1, None])

    # Create edges
    edge_trace = go.Scatter(
        x=edge_x, y=edge_y,
        line=dict(width=0.5, color='#888'),
        hoverinfo='none',
        mode='lines')

    # Create nodes
    node_x = []
    node_y = []
    node_text = []
    for node in G.nodes():
        x, y = pos[node]
        node_x.append(x)
        node_y.append(y)
        node_text.append(node)  # Display node labels

    node_trace = go.Scatter(
        x=node_x, y=node_y,
        mode='markers',
        hoverinfo='text',
        marker=dict(
            showscale=False,
            colorscale='YlGnBu',
            size=10,
            color=[],
            line_width=2))

    # Create figure
    fig = go.Figure(data=[edge_trace, node_trace],
                    layout=go.Layout(
                        title='Interactive Graph',
                        titlefont_size=16,
                        showlegend=False,
                        hovermode='closest',
                        margin=dict(b=20, l=5, r=5, t=40),
                        xaxis=dict(showgrid=False, zeroline=False, showticklabels=False),
                        yaxis=dict(showgrid=False, zeroline=False, showticklabels=False)))

    # Add node labels
    fig.update_traces(text=node_text, textposition='top center')

    # Show the interactive graph
    fig.show()

# Draw the graph
# draw_graph(G)


In [83]:

def draw_graph(graph, score_range=None):
    # Create an empty undirected graph
    G = nx.Graph()

    # Add edges and their attributes (papers) to the graph
    for keyword1 in graph:
        for keyword2 in graph[keyword1]:
            papers = graph[keyword1][keyword2]
            G.add_edge(keyword1, keyword2, papers=papers)

    # Filter nodes based on score_range
    filtered_nodes = []
    for node in G.nodes():
        if score_range is None or (graph.nodes[node]['hierarchy_score'] >= score_range[0] and graph.nodes[node]['hierarchy_score'] <= score_range[1]):
            filtered_nodes.append(node)

    # Create a subgraph containing only the filtered nodes and their connections
    H = G.subgraph(filtered_nodes)

    # Draw the graph
    pos = nx.spring_layout(H)  # Positions of nodes using the spring layout algorithm

    # Define edges and positions
    edge_x = []
    edge_y = []
    for edge in H.edges():
        x0, y0 = pos[edge[0]]
        x1, y1 = pos[edge[1]]
        edge_x.extend([x0, x1, None])  # None is used to create gaps between edge segments
        edge_y.extend([y0, y1, None])

    # Create edges
    edge_trace = go.Scatter(
        x=edge_x, y=edge_y,
        line=dict(width=0.5, color='#888'),
        hoverinfo='none',
        mode='lines')

    # Create nodes
    node_x = []
    node_y = []
    node_text = []
    for node in H.nodes():
        x, y = pos[node]
        node_x.append(x)
        node_y.append(y)
        # Constructing the text to display when hovering over a node
        text = f"{node}<br>" \
               f"Hierarchy Score: {graph.nodes[node]['hierarchy_score']}<br>" \
               f"Number of Papers: {graph.nodes[node]['num_papers']}<br>" \
               f"Age in Months: {graph.nodes[node]['age_in_months']}"
        node_text.append(text)

    node_trace = go.Scatter(
        x=node_x, y=node_y,
        mode='markers',
        hoverinfo='text',
        text=node_text,
        marker=dict(
            showscale=False,
            colorscale='YlGnBu',
            size=10,
            color=[],
            line_width=2))

    # Create figure
    fig = go.Figure(data=[edge_trace, node_trace],
                    layout=go.Layout(
                        title='Interactive Graph',
                        titlefont_size=16,
                        showlegend=False,
                        hovermode='closest',
                        margin=dict(b=20, l=5, r=5, t=40),
                        xaxis=dict(showgrid=False, zeroline=False, showticklabels=False),
                        yaxis=dict(showgrid=False, zeroline=False, showticklabels=False)))

    # Show the interactive graph
    fig.show()

# Example usage:
# Draw the entire graph
# draw_graph(G)

# Draw the graph with nodes in a specific score range
draw_graph(G, score_range=(450, 40000))

In [67]:
def unsimilar_neighbors(connections1, connections2):
    # Get the set of neighboring vertices for each vertex
    neighbors1 = set(connections1.keys())
    neighbors2 = set(connections2.keys())

    # Calculate the number of dissimilar neighboring vertices
    num_unsimilar = len(neighbors1.symmetric_difference(neighbors2))
    return num_unsimilar

def similar_neighbors(connections1, connections2):
    # Check if the neighboring vertices of two vertices are the same
    neighbors1 = set(connections1.keys())
    neighbors2 = set(connections2.keys())
    unioned_neighbors = neighbors1.intersection(neighbors2)
    return len(unioned_neighbors)

def get_pairs(graph, similar = True):
    unsimilar_pairs = []
    common_concepts = set()

    # Get the vertices in the graph
    vertices = list(graph.keys())

    # Iterate over each pair of vertices
    for i in range(len(vertices)):
        vertex1 = vertices[i]
        connections1 = graph[vertex1]
        if len(set(connections1.keys())) <= 13:
            continue
        
        common_concepts.update([vertex1])

        for j in range(i + 1, len(vertices)):
            vertex2 = vertices[j]
            connections2 = graph[vertex2]
            if len(set(connections2.keys())) <= 13:
                continue
            
            if similar:
                # Calculate the number of similar neighboring vertices
                num = similar_neighbors(connections1, connections2)
            else:
                # Calculate the number of dissimilar neighboring vertices
                num = unsimilar_neighbors(connections1, connections2)

            neighbors1 = set(connections1.keys())
            neighbors2 = set(connections2.keys())
            neighbors1.update(neighbors2)
            num = num / len(neighbors1)
            # Calculate the number of dissimilar neighboring vertices
            unsimilar_pairs.append((vertex1, vertex2, num))

    return unsimilar_pairs, common_concepts

# Get unsimilar pairs of vertices
# unsimilar_pairs, common_concepts = get_pairs(graph, similar=True)
# print(unsimilar_pairs[:10])  # Print the first 10 unsimilar pairs
# common_concepts

In [68]:
#write common concepts to file
common_concepts_path = "/home/liranc6/con_graph/common_concepts.txt"
def save_common_concepts(common_concepts_path, common_concepts):
    with open(common_concepts_path, 'w') as common_concepts_file:
        common_concepts = '\n'.join(common_concepts)    
        common_concepts_file.write(common_concepts + '\n')

save_common_concepts(common_concepts_path, common_concepts)

NameError: name 'common_concepts' is not defined

In [ ]:
#sort by the number of unsimilar neighbors from lowest to highest
unsimilar_pairs.sort(key=lambda x: x[2], reverse=False)
unsimilar_pairs[:20]

[('interpolation problem', 'binary classification', 0.0),
 ('interpolation problem', 'data analysis', 0.0),
 ('interpolation problem', 'hilbert space', 0.0),
 ('interpolation problem', 'spectral methods', 0.0),
 ('interpolation problem', 'mobile security', 0.0),
 ('interpolation problem', 'distributed systems', 0.0),
 ('interpolation problem', 'service-oriented architectures', 0.0),
 ('interpolation problem', 'workflow management', 0.0),
 ('interpolation problem', 'high-dimensional data', 0.0),
 ('interpolation problem', 'spectral analysis', 0.0),
 ('interpolation problem', 'channel state information', 0.0),
 ('interpolation problem', 'channel estimation', 0.0),
 ('interpolation problem', 'imperfect information', 0.0),
 ('interpolation problem', 'resource allocation', 0.0),
 ('interpolation problem', 'resource management', 0.0),
 ('interpolation problem', 'uncertainty modeling', 0.0),
 ('interpolation problem', 'wireless communications', 0.0),
 ('interpolation problem', 'wireless netwo

In [ ]:
# find if "Secure link formation" in the unsimilar_pairs
for pair in unsimilar_pairs:
    if "Secure link formation" in pair:
        print(pair)
        break

In [ ]:
def get_neighbours(graph, vertex):
    # Get the neighboring vertices of the vertex
    neighbors = graph[vertex]
    return list(neighbors.keys())

def find_vertex_by_name(graph, name):
    for vertex in graph:
        if str(vertex) == name:
            return vertex
    return None
# Print the neighbors of the first vertex in the unsimilar pairs
vertex = find_vertex_by_name(graph, 'coding theory')
neighbours = get_neighbours(graph, vertex)
neighbours[:30]

['computer science',
 'error correction',
 'euclidean weight',
 'extremal codes',
 'minimum weight',
 'type ii codes',
 'type ii zz2k codes',
 'upper bound on minimum weight of type ii zz2k codes',
 'zz2k codes',
 'codebook construction',
 'combinatorial optimization',
 'gaussian processes',
 'iterative algorithm',
 'modulation techniques',
 'relay networks',
 'signal processing',
 'signal-time coding',
 'wireless networks',
 'erasure codes',
 'fermat number transform',
 'fnt-based coding',
 'fnt-based reed-solomon erasure codes',
 'information dispersal algorithm (ida)',
 'mds codes',
 'reed-solomon codes',
 'reed-solomon erasure codes',
 'binary-input channels',
 'channel coding',
 'compound capacity',
 'decoding algorithms']

In [ ]:
#create a list of vertex by order of num neighbors
def get_vertex_by_num_neighbors(graph):
    vertex_by_num_neighbors = []
    for vertex in graph:
        neighbors = graph[vertex]
        num_neighbors = len(neighbors)
        vertex_by_num_neighbors.append((vertex, num_neighbors))
    vertex_by_num_neighbors.sort(key=lambda x: x[1], reverse=True)
    return vertex_by_num_neighbors

vertex_by_num_neighbors = get_vertex_by_num_neighbors(graph)
vertex_by_num_neighbors[:20]

[('machine learning', 988),
 ('graph theory', 908),
 ('algorithm design', 698),
 ('artificial intelligence', 696),
 ('distributed systems', 690),
 ('computational complexity', 658),
 ('computer science', 599),
 ('wireless networks', 530),
 ('information theory', 524),
 ('computer networks', 479),
 ('wireless communication', 471),
 ('signal processing', 397),
 ('natural language processing', 377),
 ('cryptography', 344),
 ('computer vision', 337),
 ('computational geometry', 322),
 ('approximation algorithms', 317),
 ('game theory', 316),
 ('formal language theory', 286),
 ('information retrieval', 285)]

In [ ]:
graph['normal-form games']

defaultdict(list,
            {'artificial intelligence': ['0908.2399', '0908.2399'],
             'distributed game theory': ['0908.2399', '0908.2399'],
             'dominated strategies': ['0908.2399', '0908.2399'],
             'epistemic logic systems': ['0908.2399', '0908.2399'],
             'game theory models': ['0908.2399', '0908.2399'],
             'iterated elimination': ['0908.2399', '0908.2399'],
             'iterated elimination of strictly dominated strategies': ['0908.2399',
              '0908.2399'],
             'multi-agent systems': ['0908.2399', '0908.2399'],
             'strategic reasoning': ['0908.2399', '0908.2399']})

In [ ]:
vertex_by_num_neighbors[-50:-30]

[('knowledge management processes', 9),
 ('knowledge-work support systems (kwss)', 9),
 ('transparency enhancement framework', 9),
 ('graph model', 9),
 ('affine type system', 9),
 ('higher-order computation', 9),
 ('imperative computation', 9),
 ('object spaces model', 9),
 ("scott's graph model for imperative computation", 9),
 ('state-free model', 9),
 ('syntactic control of interference', 9),
 ('typed lambda-calculus', 9),
 ('computational research', 9),
 ('immune inspired systems', 9),
 ('self-organizing networks', 9),
 ('toll-like receptors (tlr)', 9),
 ('english language processing', 9),
 ('corpus-based analysis', 9),
 ('senseval-2 challenges', 9),
 ('senseval-2 english tasks', 9)]